In [1]:
import requests
import matplotlib.pyplot as plt
import pandas as pd
import json
import re
from requests.auth import HTTPBasicAuth
from pandas import json_normalize

In [2]:
with open('../data/keys.json') as fi:
    credentials = json.load(fi)

In [3]:
api_key = credentials['etsy_key']

End goal: I am going to get the unique shop IDs for the listings found in 1331 (banners and signs), 1029 (wall hangings and mural), and 1672 (Invitations and Paper)

### 1. Paper & party supplies: Paper & Party Supplies

1250 Paper & Party Supplies count: 19717

This is too selective:
1334 Banners and signs count: 2076


1250 (Paper & Party Supplies) 

1251 (Paper)

1330 (Party Supplies)

** leads to this one: 1331 ( Party Decor)

*** leads to this one:1334 (Banners & Signs)

In [ ]:
url = 'https://api.etsy.com/v3/application/listings/active'
response = requests.get(url, headers={"x-api-key": api_key}, 
        params={'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100,
                'sort_on': ['score', 'created'],
               'taxonomy_id': [1250]})
paper_data = response.json()#['results']
paper_data

In [ ]:
flat_paper_data = pd.json_normalize(paper_data['results'])
flat_paper_data
paper_df = pd.DataFrame(flat_paper_data)
paper_df

-------------

---------------------

### 2. Home & Living: Wall Hangings & Murals

>>count: 16264

In [16]:
url = 'https://api.etsy.com/v3/application/listings/active'
response = requests.get(url, headers={"x-api-key": api_key}, 
        params={'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100,
                'sort_on': ['score', 'created'],
               'taxonomy_id': [1029]})
home_data = response.json()#['results']
home_data

{'count': 16264,
 'results': [{'listing_id': 740223621,
   'user_id': 19840612,
   'shop_id': 6766412,
   'title': 'If You Want to Change the World Go Home and Love Your Family Hand Lettered square print 12x12&quot;',
   'description': '“If you want to change the world, go home and love your family.”\n\nThis is a sweet and true Mother Teresa quote, hand lettered by yours truly.  \nIt is professionally printed at my favorite mom and pop shop, and the quality is beautiful on acid free photo paper. Every care is taken when packaged so that your print arrives in perfect condition.  Simply pop in a 12x12 frame from your local art supply/craft store, and enjoy. \n\nGreat as a meaningful gift for any holiday.  Beautiful displayed by your seasonal decor.  Lovely as a photo prop.  I offer discounts on orders of 3 or more.  (Just convo me for a custom listing.) These ship in a flat, rigid envelope.\n\nI love lettering your favorite quotes! If you like my style, and you would like me to letter on

In [ ]:
flat_home_data = pd.json_normalize(home_data['results'])

home_df = pd.DataFrame(flat_home_data)
home_df

### 3. Weddings: Invitations and Paper
>>Count: 1897

In [4]:
url = 'https://api.etsy.com/v3/application/listings/active'
response = requests.get(url, headers={"x-api-key": api_key}, 
        params={'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100,
                'sort_on': ['score', 'created'],
               'taxonomy_id': [1672]})
wed_data = response.json()#['results']
wed_data

{'count': 1874,
 'results': [{'listing_id': 119919686,
   'user_id': 17415724,
   'shop_id': 7371868,
   'title': 'Dom Loves Mary Pro Calligraphy Font',
   'description': 'Dom Loves Mary Pro Calligraphy Font is  three fonts in one!  Mix and match letters to create a custom look!\r\n\r\nHand lettered with a timeless, classic look. In addition to the wide variety of letters, the PRO font contains 250 flourishes and a selection of decorative ornaments.  (These can only be accessed if you are using a program that is OPEN TYPE CAPABLE). All of this is offered at a 42% savings!\r\n\r\nWhich of the Dom Loves Mary Fonts is for me?  \r\nIt depends on the program you&#39;re using and the amount of additional characters you want to have access to.\r\n\r\nIf you are using OPEN TYPE CAPABLE PROGRAMS like Illustrator or InDesign: \r\nYou can purchase ANY of the Dom Loves Mary fonts.  You will have full access to ALL of the additional letters, flourishes and ornaments in the glyph panel.\r\n\r\nIf yo

In [ ]:
flat_wed_data = pd.json_normalize(wed_data['results'])

wed_df = pd.DataFrame(flat_wed_data)
wed_df

###  X 4. Art & Collectibles

this is not quite the right style

In [ ]:
url = 'https://api.etsy.com/v3/application/listings/active'
response = requests.get(url, headers={"x-api-key": api_key}, 
        params={'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100,
                'sort_on': ['score', 'created'],
               'taxonomy_id': [102]})
data = response.json()#['results']
data

------------

# Lets take a deeper look into the shop IDs attached to these listings

In [ ]:
unique_paper_id = paper_df['shop_id'].unique().tolist()
unique_paper_id

In [ ]:
len(unique_paper_id)

In [ ]:
unique_home_id = home_df['shop_id'].unique().tolist()
unique_home_id

In [ ]:
len(unique_home_id)

In [ ]:
unique_wed_id = wed_df['shop_id'].unique().tolist()
unique_wed_id

In [ ]:
len(unique_wed_id)

In [ ]:
all_shop_ids = unique_wed_id + unique_home_id + unique_paper_id
all_shop_ids


In [ ]:
len(all_shop_ids)

In [ ]:
import numpy as np

In [ ]:
output = []
for x in all_shop_ids:
    if x not in output:
        output.append(x)
output

In [ ]:
len(output)

## Loop to grab all listings with specific parameters and taxonomy ids

##### 1. Loop for Paper & Party

In [6]:
import time

In [ ]:
url = 'https://api.etsy.com/v3/application/listings/active'
start = 100          # Start at 0
chunk_size = 100     # Fetch 100 rows at a time
paper_listings = paper_data['results']   # Empty out our result list
#paper_listings.append(paper_data['results'])   #add results(key) to listings array

while True:
        # Fetch the set of records starting at 'start'
    response = requests.get(
        url,
        headers={"x-api-key": api_key}, 
        params={
            'keywords': [
                'calligraphy',
                'handwritten',
                'handlettering',
                'handlettered',
                'hand lettered'
            ], 
            'sort_order': 'ascending',
            'limit': chunk_size,
            'offset': start,
            'sort_on': ['score', 'created'],
            'taxonomy_id': 1250
        }
    )
        #turn response from above into json file type
    json_response = response.json()
        #take results_key and add it to listings to create full data frame results   
    paper_listings.extend(json_response['results'])
        # Move up the starting record
    start = start + chunk_size
        #pause loop to limit risk of running into Etsy's API rate limit
    time.sleep(0.3) # Seconds
        # If we have fetched all of the records, bail out
    if (start > 12000):
        break
        
 #Convert the list into a data frame
paper_listings

In [ ]:
url = 'https://api.etsy.com/v3/application/listings/active'
start = 12000       # Start at 12k this time since we already have that 
chunk_size = 100     # Fetch 100 rows at a time
paper_listings_ext = paper_listings   # Empty out our result list
#paper_listings.append(paper_data['results'])   #add results(key) to listings array

while True:
        # Fetch the set of records starting at 'start'
    response = requests.get(
        url,
        headers={"x-api-key": api_key}, 
        params={
            'keywords': [
                'calligraphy',
                'handwritten',
                'handlettering',
                'handlettered',
                'hand lettered'
            ], 
            'sort_order': 'ascending',
            'limit': chunk_size,
            'offset': start,
            'sort_on': ['score', 'created'],
            'taxonomy_id': 1250
        }
    )
        #turn response from above into json file type
    json_response = response.json()
        #take results_key and add it to listings to create full data frame results   
    paper_listings_ext.extend(json_response['results'])
        # Move up the starting record
    start = start + chunk_size
        #pause loop to limit risk of running into Etsy's API rate limit
    time.sleep(0.3) # Seconds
        # If we have fetched all of the records, bail out
    if (start > 12000):
        break
        
 #Convert the list into a data frame
paper_listings_ext

In [ ]:
print(start)

In [ ]:
len(paper_listings)

In [ ]:
len(paper_listings_ext)

In [ ]:
paper_listings_shop_id = paper_listings[1]
paper_listings_shop_id

In [ ]:
#flat_id=list()
#for sub_list in paper_listings2:
    #flat_id += sub_list
#paper_id_flat = flat_id

deeper_paperid = pd.json_normalize(paper_listings)
deeper_paperid

In [ ]:
deeper_paperid.to_csv('paper_listings.csv')

#### 2. Wedding taxonomy id

In [10]:
url = 'https://api.etsy.com/v3/application/listings/active'
start = 100          # Start at 0
chunk_size = 100     # Fetch 100 rows at a time
wed_listings = wed_data['results']   # Empty out our result list
#paper_listings.append(paper_data['results'])   #add results(key) to listings array

while True:
        # Fetch the set of records starting at 'start'
    response = requests.get(
        url,
        headers={"x-api-key": api_key}, 
        params={
            'keywords': [
                'calligraphy',
                'handwritten',
                'handlettering',
                'handlettered',
                'hand lettered'
            ], 
            'sort_order': 'ascending',
            'limit': chunk_size,
            'offset': start,
            'sort_on': ['score', 'created'],
            'taxonomy_id': 1672
        }
    )
        #turn response from above into json file type
    json_response = response.json()
        #take results_key and add it to listings to create full data frame results   
    wed_listings.extend(json_response['results'])
        # Move up the starting record
    start = start + chunk_size
        #pause loop to limit risk of running into Etsy's API rate limit
    time.sleep(0.35) # Seconds
        # If we have fetched all of the records, bail out
    if (start > 800):
        break
        
 #Convert the list into a data frame
wed_listings

[{'listing_id': 119919686,
  'user_id': 17415724,
  'shop_id': 7371868,
  'title': 'Dom Loves Mary Pro Calligraphy Font',
  'description': 'Dom Loves Mary Pro Calligraphy Font is  three fonts in one!  Mix and match letters to create a custom look!\r\n\r\nHand lettered with a timeless, classic look. In addition to the wide variety of letters, the PRO font contains 250 flourishes and a selection of decorative ornaments.  (These can only be accessed if you are using a program that is OPEN TYPE CAPABLE). All of this is offered at a 42% savings!\r\n\r\nWhich of the Dom Loves Mary Fonts is for me?  \r\nIt depends on the program you&#39;re using and the amount of additional characters you want to have access to.\r\n\r\nIf you are using OPEN TYPE CAPABLE PROGRAMS like Illustrator or InDesign: \r\nYou can purchase ANY of the Dom Loves Mary fonts.  You will have full access to ALL of the additional letters, flourishes and ornaments in the glyph panel.\r\n\r\nIf you are using LIMITED (Photoshop) 

In [12]:
start

200

In [13]:
len(wed_listings)

5622

In [14]:
deeper_wed = pd.json_normalize(wed_listings)
deeper_wed

listing_id    user_id   shop_id  \
0      119919686   17415724   7371868   
1      473572414   17098880   6823707   
2      802444924   18096930  15943136   
3      255960471   66215956  11630683   
4      584087059  100636681  14008975   
...          ...        ...       ...   
5617  1177227945   19098480  16482469   
5618   624644923   44787026   9201026   
5619   597614189    7449966   5557878   
5620   781688653  106564559  18945582   
5621   881858562  306385682  23331069   

                                                  title  \
0                   Dom Loves Mary Pro Calligraphy Font   
1     Flourished Calligraphy Place Card | Wedding | ...   
2     Custom Envelope Calligraphy Addressing // for ...   
3     Envelope Address Calligraphy // Handwritten Ad...   
4     Printable OR Printed Picture Thank You Postcar...   
...                                                 ...   
5617  Laser Cut Acrylic Name | Custom Hand Lettered ...   
5618  Marble Hexagon Escort Cards, Modern Wedding, M...   
5619  Let&#39;s Celebrate, Congrats, Congratulations...   
5620   Valentine&#39;s Day, Hand Lettered Greeting Card   
5621  Hand Lettered Calligraphy Card on a Watercolou...   

                                            description   state  \
0     Dom Loves Mary Pro Calligraphy Font is  three ...  active   
1     Professionally hand-lettered calligraphy place...  active   
2     Custom envelope addressing in traditional call...  active   
3     Calligraphy / Hand lettered name(s) and addres...  active   
4     Printable OR Printed Photo Thank You Postcards...  active   
...                                                 ...     ...   
5617  DETAILS:\nLevel up your place settings with th...  active   
5618  **Please do not purchase this listing. Message...  active   
5619  Let&#39;s celebrate! It&#39;s time to celebrat...  active   
5620  &quot;Happy Valentine&#39;s Day&quot;\n\nSend ...  active   
5621  Each item is hand lettered by myself. I paint ...  active   

      creation_timestamp  created_timestamp  ending_timestamp  \
0             1604090463         1604090463        1614548463   
1             1604102452         1604102452        1614560452   
2             1622521881         1622521881        1633062681   
3             1627630835         1627630835        1638261635   
4             1635463942         1635463942        1646094742   
...                  ...                ...               ...   
5617          1646545630         1646545630        1657082830   
5618          1646572830         1646572830        1657110030   
5619          1646575863         1646575863        1657113063   
5620          1646581831         1646581831        1657119031   
5621          1646583043         1646583043        1657120243   

      original_creation_timestamp  ...  file_data  has_variations  \
0                      1357690196  ...      1 ZIP           False   
1                      1477190359  ...                       True   
2                      1590698540  ...                       True   
3                      1447392527  ...                       True   
4                      1515098799  ...                       True   
...                           ...  ...        ...             ...   
5617                   1644556208  ...                       True   
5618                   1530490189  ...                       True   
5619                   1520015177  ...                      False   
5620                   1582592006  ...                       True   
5621                   1604087352  ...                      False   

      should_auto_renew  language  taxonomy_id  production_partners skus  \
0                  True     en-US         1675                   []   []   
1                  True     en-US         6056                   []   []   
2                  True     en-US         1676                   []   []   
3                  True     en-US         1676                   []   []   
4        

In [15]:
deeper_wed.to_csv('wed_listings.csv')

#### 3. Home listings loop

In [20]:
url = 'https://api.etsy.com/v3/application/listings/active'
start = 100          # Start at 0
chunk_size = 100     # Fetch 100 rows at a time
home_listings = home_data['results']   # Empty out our result list
#paper_listings.append(paper_data['results'])   #add results(key) to listings array

while True:
        # Fetch the set of records starting at 'start'
    response = requests.get(
        url,
        headers={"x-api-key": api_key}, 
        params={
            'keywords': [
                'calligraphy',
                'handwritten',
                'handlettering',
                'handlettered',
                'hand lettered'
            ], 
            'sort_order': 'ascending',
            'limit': chunk_size,
            'offset': start,
            'sort_on': ['score', 'created'],
            'taxonomy_id': 1029
        }
    )
        #turn response from above into json file type
    json_response = response.json()
        #take results_key and add it to listings to create full data frame results   
    home_listings.extend(json_response['results'])
        # Move up the starting record
    start = start + chunk_size
        #pause loop to limit risk of running into Etsy's API rate limit
    time.sleep(0.35) # Seconds
        # If we have fetched all of the records, bail out
    if (start > 10000):
        break
        
 #call results
home_listings

[{'listing_id': 740223621,
  'user_id': 19840612,
  'shop_id': 6766412,
  'title': 'If You Want to Change the World Go Home and Love Your Family Hand Lettered square print 12x12&quot;',
  'description': '“If you want to change the world, go home and love your family.”\n\nThis is a sweet and true Mother Teresa quote, hand lettered by yours truly.  \nIt is professionally printed at my favorite mom and pop shop, and the quality is beautiful on acid free photo paper. Every care is taken when packaged so that your print arrives in perfect condition.  Simply pop in a 12x12 frame from your local art supply/craft store, and enjoy. \n\nGreat as a meaningful gift for any holiday.  Beautiful displayed by your seasonal decor.  Lovely as a photo prop.  I offer discounts on orders of 3 or more.  (Just convo me for a custom listing.) These ship in a flat, rigid envelope.\n\nI love lettering your favorite quotes! If you like my style, and you would like me to letter one for you, convo me for a quote! 

In [21]:
len(home_listings)

22900

In [22]:
deeper_home = pd.json_normalize(home_listings)
deeper_home

listing_id    user_id   shop_id  \
0       740223621   19840612   6766412   
1       490998782   38954524   8718556   
2       518644764  101112796  14333509   
3       644931979  162226534  18110774   
4       581224258  121658751  15800102   
...           ...        ...       ...   
22895   261388948   66332651  11122726   
22896   677597909  164992388  18247331   
22897  1039397866    8775449  13286623   
22898   209153170   39086621   8734605   
22899   508765582   23654923   7148172   

                                                   title  \
0      If You Want to Change the World Go Home and Lo...   
1      Digitized Art (not a mug): Love, For God so lo...   
2      They Broke Bread Sign - Acts 2:46 - Wood Sign ...   
3      Scripture Wall Art Bible Verse Wall Art Bible ...   
4      Hand Lettered Word of the Year - Service  - IN...   
...                                                  ...   
22895  Life is Beautiful Downloadable Print, Gold Let...   
22896  Cupid&#39;s Sparrow Hand-lettered watercolor a...   
22897  Don&#39;t stress over what you can&#39;t contr...   
22898  Inspirational Wall Art, No One Can Make You Fe...   
22899  Our Lovely Home Typography Print - Hand Letter...   

                                             description   state  \
0      “If you want to change the world, go home and ...  active   
1      IMPORTANT NOTE:  THIS IS NOT A MUG FOR SALE, B...  active   
2      ~BROKE BREAD SIGN~ Wooden Decorative Inspirati...  active   
3      Psalm 46:10 Bible Quote Print Bible Verses Pri...  active   
4      Hand Lettered Word of the Year - Service - INS...  active   
...                                                  ...     ...   
22895  Downloadable digital print only. No items will...  active   
22896  One of many Michael Scott quotes where he&#39;...  active   
22897  DON&#39;T STRESS OVER WHAT YOU CAN&#39;T CONTR...  active   
22898  &quot;No one can make you feel inferior withou...  active   
22899  This simple and stylish personalised home prin...  active   

       creation_timestamp  created_timestamp  ending_timestamp  \
0              1603860710         1603860710        1614491510   
1              1603901527         1603901527        1614532327   
2              1603902858         1603902858        1614533658   
3              1603914077         1603914077        1614544877   
4              1603928444         1603928444        1614559244   
...                   ...                ...               ...   
22895          1652245819         1652245819        1662873019   
22896          1652246409         1652246409        1662873609   
22897          1652248209         1652248209        1662875409   
22898          1652248220         1652248220        1662875420   
22899          1652253032         1652253032        1662880232   

       original_creation_timestamp  ...            file_data  has_variations  \
0                       1569626579  ...                                False   
1                       1484099215  ...                2 PDF           False   
2                       1495501391  ...                                 True   
3                       1537337753  ...  2 ZIP, 1 JPG, 1 PDF           False   
4                       1519080145  ...                2 PDF           False   
...                            ...  ...                  ...             ...   
22895                   1450753942  ...         1 JPG, 1 PNG           False   
22896                   1548360482  ...                                 True   
22897                   1626590262  ...         1 JPG, 1 PDF           False   
22898                   1414707727  ...                                 True   
22899                   1491231628  ...                                 True   

       should_auto_renew  language  taxonomy_id  production_partners skus  \
0                  False     en-US         2078                   []   []   
1                   True     en-US          119         

In [23]:
deeper_home.to_csv('home_listings.csv')

## FOR loop to insert list of unique shop_ids found in each taxonomy call. 
May need to wait to use this until we have all of the data but at least we know it works.

In [ ]:
shop_id_listings = []

for x in unique_shop_id:
    url_shop_id = 'https://api.etsy.com/v3/application/shops/%s'%x
    response_shop = requests.get(url_shop_id, headers={"x-api-key": api_key}, 
        params={#'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100})
               #'taxonomy_id': [1250, 1330, 1331, 1334]
    data_shop = response_shop.json()#['results']
    shop_id_listings.append(data_shop)

In [ ]:
shop_id_listings

###### This gets thru the first list [ ] we created

In [ ]:
shop_id2 = shop_id_listings[1]
shop_id3 = shop_id2['results']
shop_data = pd.json_normalize(shop_id3, max_level=2)
shop_data

In [ ]:
flat_id=list()
for sub_list in shop_id3:
    flat_id += sub_list
id_flat = flat_id

deeper_id_flat = pd.json_normalize(id_flat)
deeper_id_flat


start = 100             # Start at 0
chunk_size = 100     # Fetch 100 rows at a time
listings =[]           # Empty out our result list
listings.append(data['results'])   #add results(key) to listings array

while True:
            # Fetch the set of records starting at 'start'
        response = requests.get(url, headers={"x-api-key": api_key}, params={'keywords': 'Calligraphy', 'limit': chunk_size, 'offset': start})
            #turn response from above into json file type
        json_response = response.json()
            #take results_key and add it to listings to create full data frame results   
        listings.append(json_response['results'])
            # Move up the starting record
        start = start + chunk_size
            # If we have fetched all of the records, bail out
        if (start > 900):
            break
        
 #Convert the list into a data frame
listings

In [ ]:
flat_shop_id= pd.json_normalize(shop_id_listings['results'])
flat_shop_id

In [ ]:
url_shop_id = 'https://api.etsy.com/v3/application/shops/9039454/listings/active'
response_shop = requests.get(url_shop_id, headers={"x-api-key": api_key}, 
        params={'keywords': ['calligraphy', 'handwritten', 'handlettering', 'handlettered', 'hand lettered'], 
                'sort_order': 'ascending', 
                'limit': 100,
               'taxonomy_id': [1250, 1330, 1331, 1334]})
data_shop = response_shop.json()#['results']
data_shop